## Finding Fake/Duplicate Records

Commonly known as Data Dedupication & Record Linkage

In [2]:
# Download and unzip data
# !wget http://data.insideairbnb.com/united-kingdom/england/london/2023-03-14/data/listings.csv.gz -P ../data/
# !gunzip -kf ../data/listings.csv.gz

In [3]:
# !pip install nltk

In [4]:
import nltk
nltk.download('stopwords')
nltk.download('punkt')
import random

[nltk_data] Downloading package stopwords to
[nltk_data]     /home/eessnin/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to /home/eessnin/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [20]:
from datetime import datetime, date
import pandas as pd
import numpy as np
import string
import re
from sklearn.feature_extraction.text import TfidfVectorizer
import re
import string

%matplotlib inline

In [6]:
df = pd.read_csv('../data/listings.csv')

In [7]:
df.head()

id                                      listing_url  \
0  714569379355913481  https://www.airbnb.com/rooms/714569379355913481   
1  808038970516277767  https://www.airbnb.com/rooms/808038970516277767   
2  822557738577472503  https://www.airbnb.com/rooms/822557738577472503   
3             3518856             https://www.airbnb.com/rooms/3518856   
4             4876550             https://www.airbnb.com/rooms/4876550   

        scrape_id last_scraped       source  \
0  20230314070633   2023-03-14  city scrape   
1  20230314070633   2023-03-14  city scrape   
2  20230314070633   2023-03-14  city scrape   
3  20230314070633   2023-03-14  city scrape   
4  20230314070633   2023-03-14  city scrape   

                                                name  \
0            Lovely private bedroom in Muswell Hill.   
1                       Studio Flat  Franklin London   
2   PropertyPlug - 2Bed Flat in Edgware SmartTV WiFi   
3                   Wimbledon Double Bedroom Ensuite   
4  Stunning Apartment 2 minutes walk to Tube Station   

                                         description neighborhood_overview  \
0    Take a break and unwind at this peaceful oasis.                   NaN   
1  Brand New Modern Kitchen<br />Close to Excelle...                   NaN   
2  Enjoy easy access to everything from this perf...                   NaN   
3  A welcoming and stylish 2 bedroom 2 bathroom f...                   NaN   
4  Luxury Modern Apartment in modern development ...                   NaN   

                                         picture_url    host_id  ...  \
0  https://a0.muscache.com/pictures/miso/Hosting-...   39009854  ...   
1  https://a0.muscache.com/pictures/miso/Hosting-...  495977998  ...   
2  https://a0.muscache.com/pictures/d77957d5-695a...  325629338  ...   
3  https://a0.muscache.com/pictures/23a18442-fc1d...     187811  ...   
4  https://a0.muscache.com/pictures/miso/Hosting-...   25087384  ...   

  review_scores_communication review_scores_location review_scores_value  \
0                         NaN                    NaN                 NaN   
1                         NaN                    NaN                 NaN   
2                         NaN                    NaN                 NaN   
3                         5.0                   3.67                3.67   
4                         NaN                    NaN                 NaN   

  license instant_bookable calculated_host_listings_count  \
0     NaN                f                              1   
1     NaN                t                              7   
2     NaN                t                              4   
3     NaN                f                              2   
4     NaN                f                              1   

  calculated_host_listings_count_entire_homes  \
0                                           0   
1                                           7   
2                                           4   
3                                           0   
4                                           1   

  calculated_host_listings_count_private_rooms  \
0                                            1   
1                                            0   
2                                            0   
3                                            2   
4                                            0   

  calculated_host_listings_count_shared_rooms reviews_per_month  
0                                           0               NaN  
1                                           0               NaN  
2                                           0               NaN  
3                                           0              0.05  
4                                           0               NaN  

[5 rows x 75 columns]

In [8]:
# Since this is a data deduplication problem, we're interested in data uploaded by the host, let's print list of columns to find out those columns
df.shape

(75241, 75)

In [9]:
# Fillna
df['name'].fillna('', inplace=True)
df['description'].fillna('', inplace=True)

In [21]:
# tfidf calculation
text_content = df['name'] + ' ' + df['description']

#remove HTML tags
text_content = text_content.str.replace(r'<[^<>]*>', '', regex=True)

# Create vectorizer
vector = TfidfVectorizer(max_df=0.3,         # drop words that occur in more than X percent of documents
                             #min_df=8,      # only use words that appear at least X times
                             stop_words='english', # remove stop words
                             lowercase=True, # Convert everything to lower case 
                             use_idf=True,   # Use idf
                             norm=u'l2',     # Normalization
                             smooth_idf=True # Prevents divide-by-zero errors
                            )
tfidf = vector.fit_transform(text_content)

In [24]:
tfidf.shape

(75241, 65039)

In [22]:
# Request function : search the top_n articles from a request ( request = string)
def search(tfidf_matrix,model,request, top_n = 5):
    request_transform = model.transform([request])
    similarity = np.dot(request_transform,np.transpose(tfidf_matrix))
    x = np.array(similarity.toarray()[0])
    indices=np.argsort(x)[-5:][::-1]
    return indices, x[indices]

# Find similar : get the top_n articles similar to an article 
# def find_similar(tfidf_matrix, index, top_n = 5):
#     cosine_similarities = linear_kernel(tfidf_matrix[index:index+1], tfidf_matrix).flatten()
#     related_docs_indices = [i for i in cosine_similarities.argsort()[::-1] if i != index]
#     return [index for index in related_docs_indices][0:top_n]    

# Print the result
def print_result(ind, request_content, indices, scores, X, min_score = 0.5):
    print('\nSearch : ' + str(ind) + ', ' + request_content)
    print('\nBest Results :')
    no_match = True
    r = 0
    for i in range(len(indices)):
        if (scores[i] > min_score) and (ind != indices[i]):
            no_match = False
            print('\nid = {0:5d} - {1} -> {2}'.format(indices[i], scores[i], X.loc[indices[i]]))
            r += 1
    if no_match:
        print('None')
    return r

In [25]:
# Minimum similarity score to qualify record as a match
import time
s = time.time()
MIN_MATCH_THRESHOLD = 0.8
# Number of tests to conduct 
NUM_RANDOM_TESTS = 7500
test_indices = random.sample(range(len(text_content)), NUM_RANDOM_TESTS)
c = 0
for ind in test_indices:
    print("---------------------------------------")
    request = text_content[ind]
    result, scores = search(tfidf,vector, request, top_n = 5)
    r = print_result(ind, request, result, scores, text_content, min_score=MIN_MATCH_THRESHOLD)
    c += r
    print("---------------------------------------")
    
print("No of random sample tested", NUM_RANDOM_TESTS)
print("Total matches found", c)
print("Time taken(s)", int(time.time()-s))

---------------------------------------

Search : 31970, Luxury flat at a garden square. Luxury flat facing fabulous Kensington private garden square.Located at one of the most prestigious garden squares in Kensington, this two double bedroom, two bathrooms apartment is perfect for guests wanting to enjoy London or doing some shopping. There is a fully equipped kitchen with all the mod cons, a TV with satellite channels, a living room, two bathrooms with shower and toilet, one en-suite and  an office area with a desk and internet. It benefits from a large lounge and dining area.

Best Results :
None
---------------------------------------
---------------------------------------

Search : 20917, Lovely 2 BDR house w/garden & parking in Greenwich Welcome to my spacious semi-detached house with two bedrooms, 1,5 bathrooms, and a living room. The flat comes with its own parking and garden at the back. It is located in a quiet street, close to amenities and restaurants. Easy access to centr


Search : 70566, Room Double inclusive of 40" HD TV A good size luxury room inclusive of 40" Smart HD TV, 3 Seater Sofa, Coffee table, Chair and Double Bed. Room is suitable for a single person or a couple. Barking town center is close by for shopping and traveling by bus or train.The spaceThere is access to front garden through the room to enjoy sunlight throughout the day.Guest accessMy guests can access to the kitchen for self catering to make themselves feel like there own house.Other things to noteI hope you will enjoy your stay in a friendly environment.

Best Results :
None
---------------------------------------
---------------------------------------

Search : 54953, Stylish and cosy Studio flat in Central London Amazing studio flat in Central London, very stylish, cosy, has everything you need for a stay in London. A lovely place to enjoy your city or business break. Just round the corner from Hyde Park, 1 minute away from Lancaster Gate tube and 3 minutes away from Paddingto


Search : 12721, Natural light in modern studio A modern and spacious apartment close to the bars and restaurants of Brixton, as well as Brockwell Park. Peaceful and safe, with plenty of light. A private balcony for morning coffee or evening drinks, separate bedroom and bathroom, and a full kitchen. A piano too.The spaceThis is my home that you’re welcome to stay in while I’m away. You’ll find it has more character than a dedicated rental property - there is a piano and books to read. It has a little wear and tear in places, which I mention out of transparency, but will be spotlessly clean for your stay. The main room is large with big windows, allowing plenty of natural light and views of the sky. It has a dining table, chairs, comfortable sofa. There is a full working kitchen with electric hob and oven for your to self-cater, as well as washing machine. A separate bedroom has plenty of storage for your luggage. The modern bathroom has a shower with excellent water pressu

Best Result


Search : 38324, 2 Bed Flat-Canning Town, O2 & Excel-London We welcome Families, Groups & Business Travellers. 2-bedroom ground floor apartment in London - Canning town/Plaistow.✪ Sleeps Up to 4 Guests✪ 2 Bedroom Flat✪ 4 Beds (1 Double bed, 2 Single beds & Sofa bed)✪ Fully Equipped Kitchen✪ 1 Bathroom✪ Professionally Cleaned Apartment✪ Free Wi-Fi & Parking✪ Smart TV with Netflix✪ Computer Chair and Desk✪ Situated in the ideal area in Plaistow/Barking Road and with easy access links to A13, A112, A124 and close Black wall tunnelThe space✪ Special Discounts on LONG TERM Bookings. ✪ ➞ Comfortable & Cozy home.➞ 2 Bedroom House in Fairbairn, Greater London, Essex is just a short 10 mins walk to the Canning town station and Plaistow Station.➞ Top attractions are 8 miles away Tower of London, Sky Garden, Tower Bridge, Trafalgar Square, Big Ben, Harrods, Hype Park, Buckingham Palace.➞ Reach Canary Wharf, Excel, O2 and  St

Best Results :
None
---------------------------------------
-----------


Search : 30769, Bright, Spacious Flat for 2 near Camden Town This spacious & bright 1-bedroom flat for 2 is walking distance from Kings Cross or Camden Town. It offers complete amenities and is within easy reach of the many food and retail establishments around Camden, including the famous markets or the upmarket shopping and restaurants of Granary square. Guests can easily use public transport from Camden Road Station, Camden Underground station and Kings Cross station to get to their destination or attraction of choice.The spaceIn addition to the great location (walking distance to Kings Cross and Camden) this spacious and sunny 1-bedroom flat that’s perfect for 2. It has a double bed and is well-appointed to offer guests full amenities during their stay. It also has a lovely garden overlooking Regents canal. The house is in a lovely quiet cul de sac with almost no road noise, a rare find for London.Guest accessGuests will have access to the entire house.Other things to note<

Best 

...


Search : 24941, Enjoy space in an amazing 2bed/2bath -south London Within a new built and with modern amenities, this is a surprisingly large 2bed/2bath located in the Little Portugal area. Conveniently located within walking distance from Stockwell, Wandsworth Rd and the new Nine Elms stations, this is an ideal place for a family in need of space or for business travellersIt is large and spacious and fully equipped with a living / kitchen / dining area to enjoy togetherLocated on a basement floor but with an outdoor space that brings in a lot of lightThe spaceThis is a newly refurbished apartment which is located on the basement floor of a recently renovated building. It features a small patio which brings light in the apartment, so it does not feel like a basementIt is located on Wandsworth Road. You will find amenities such as convenience store and the post office near the building, as well as near Larkhall ParkThe apartment's main space is surprisingly large. It contains a fu

Bes


Search : 25572, Cozy studio flat nearby tube (6) Take a break and unwind at this peaceful oasis.

Best Results :

id = 43545 - 0.868165796306559 -> These is my cozy house. Take a break and unwind at this peaceful oasis.

id =  3825 - 0.8261607466915907 -> Room in London Take a break and unwind at this peaceful oasis.

id = 57149 - 0.8261607466915907 -> 2 bedroom flat Take a break and unwind at this peaceful oasis.

id = 49357 - 0.80370334491275 -> Cozy, separate bedroom in a family home. Take a break and unwind at this peaceful oasis.
---------------------------------------
---------------------------------------

Search : 27504, The Paddington Hideout - Amazing 2BDR Flat + Patio This modern two-bed in one of London's most sought-after neighbourhoods offers convenient transport links and has a vast amount of attractions in walking distance, as well as shops, magnificent restaurants, bars. The open plan kitchen and living area make this home a great place to relax. The apartment is cur


Best Results :
None
---------------------------------------
---------------------------------------

Search : 12349, 2 bed apartment w/ private garden in South London This lovely two bedroom flat is located in the heart of South London in Brockley. It's close by beautiful parks like Telegraph Hill but also a very short walk to public transportation (5 minutes to Brockley Station overground which easily connects to the tube).The flat is stylish and spacious compared to most London tiny apartments. It feels more like a home. It's a two floor flat with two bedrooms, a private garden, large kitchen and updated fixtures.

Best Results :
None
---------------------------------------
---------------------------------------

Search : 31346, Swinton St Apartment 3 This is a comfortable 1 bedroom apartment on the top floor of a typical Victorian 3 storey London house with a lovely south facing sitting/kitchen/dining area. It is fully furnished mainly from IKEA and is very comfortable but not ove


Search : 22594, Newly Refurbished 2 Bedroom, Family Apartment! Newly renovated 2 bedroom apartment overlooking the Olympic Stadium. Walking distance to Stratford Station and Westfield. This apartment is located in a secured gated community.Apartment Includes:> Wifi> New Beddings> Smart TV with Netflix> Cutlery and Dishes> Toiletries> Shared Gym> Shared Sauna> 2 Bedrooms, 2 Double Beds> 1 En-suite > 1 Family Bathroom

Best Results :
None
---------------------------------------
---------------------------------------

Search : 7660, Light, Airy welcoming flat in Kensal Rise My place is close to Kensal Green Underground station and Kensal Rise overground. It is a 10 minute bus ride from Portobello and Notting Hill Gate Station.. You’ll love my place because it is flooded with light, has beautiful high ceilings and is so easy to get to and from. It is relaxed but beautifully decorated with a modern/ bohemian feel. My place is good for couples, friends and families traveling together.

Bes


Search : 49403, Bohemian gem in Primrose Hill Bohemian first flat overlooking Primrose Hill. The bright and spacious living room has high ceilings and original victorian mouldings, three large windows access a balcony with a beautiful view of the park. The flat with a single bedroom and a large double sofa-bed can accomodate up to three guests. The bathroom (bath only) is exclusive to the flat but accessible through the landing. Small pets are allowed upon landlord's approval and at an extra fee of £10 per day.

Best Results :

id = 49041 - 0.9200039138987153 -> Amazing park view apartment in Primrose Hill Bright and spacious bohemian first floor flat overlooking the park in Primrose Hill. The  living room has high ceilings and original victorian mouldings, three large windows access a balcony with a beautiful view of the park. The flat with a single bedroom and a large double sofa-bed can accomodate up to three guests. The bathroom is on the landing outside the flat (bath only) but i